In [2]:
!pip install -U spacy download en_core_web_sm

In [4]:
!pip install  presidio_analyzer
!pip install  presidio_anonymizer
!pip install faker

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 85.7/85.7 kB 1.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 97.7/97.7 kB 8.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.6/2.6 MB 18.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 11.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 8.6 MB/s eta 0:00:00


### **ran again with 3000 elements for time limit there are more emails if we use thewhole dataset
**

In [4]:
import csv
from presidio_analyzer import AnalyzerEngine
from presidio_anonymizer import AnonymizerEngine
import re
from faker import Faker

fake = Faker()

analyzer = AnalyzerEngine()
anonymizer = AnonymizerEngine()

# Regular expression patterns to identify different types of PII
email_pattern = r'\b[A-Za-z0-9._%+-]+@[A-Za-z0-9.-]+\.[A-Z|a-z]{2,}\b'

# Define the function to anonymize PII in a given text
def anonymize_text(text, analyzer_results):
    pii_entities = [(entity.entity_type, entity.start, entity.end) for entity in analyzer_results]
    masked_text = text  # Initialize masked text with the original text

    # Anonymize names and emails
    for entity in analyzer_results:
        if entity.entity_type == "PERSON" and entity.start >= 0 and entity.end <= len(text):
            fake_name = fake.name()
            masked_text = masked_text[:entity.start] + fake_name + masked_text[entity.end:]
        elif entity.entity_type == "EMAIL_ADDRESS" and entity.start >= 0 and entity.end <= len(text):
            fake_email = fake.email()
            masked_text = masked_text[:entity.start]  + "**************" + masked_text[entity.end:]

    return masked_text, pii_entities

processed_rows = []
processed_rows_sent = []

with open('IMDB.csv', mode='r', newline='', encoding='utf-8') as csvfile:
    reader = csv.reader(csvfile)


    entity_type_counts = {}

    rows_processed =0

    for row in reader:
        row_str = ','.join(row)

        last_comma_index = row_str.rfind(',')
        review = row_str[:last_comma_index].strip()
        sentiment = row_str[last_comma_index + 1:].strip()


        analyzer_results =analyzer.analyze(review, language='en')


        email_matches = re.findall(email_pattern, review)


        pii_entities = [('EMAIL_ADDRESS', review.find(email), review.find(email) + len(email)) for email in email_matches]


        anonymize_results= anonymize_text(review, analyzer_results)

        anonymized_review= anonymize_results[0]
        pii_entities.extend(anonymize_results[1])

        for entity, _, _ in pii_entities:
             entity_type_counts[entity] = entity_type_counts.get(entity, 0) + 1

        print("Original Review:", review)
        print("Anonymized Review:", anonymized_review)

        processed_rows.append(anonymized_review)
        processed_rows_sent.append(sentiment)

        print("Detected PII entities:")
        print(pii_entities)


        rows_processed += 1

        if rows_processed >= 3000:
            break



Original Review: Review
Anonymized Review: Review
Detected PII entities:
[]
Original Review: One of the other reviewers has mentioned that after watching just 1 Oz episode you'll be hooked. They are right, as this is exactly what happened with me.<br /><br />The first thing that struck me about Oz was its brutality and unflinching scenes of violence, which set in right from the word GO. Trust me, this is not a show for the faint hearted or timid. This show pulls no punches with regards to drugs, sex or violence. Its is hardcore, in the classic use of the word.<br /><br />It is called OZ as that is the nickname given to the Oswald Maximum Security State Penitentary. It focuses mainly on Emerald City, an experimental section of the prison where all the cells have glass fronts and face inwards, so privacy is not high on the agenda. Em City is home to many..Aryans, Muslims, gangstas, Latinos, Christians, Italians, Irish and more....so scuffles, death stares, dodgy dealings and shady agreem

Original Review: I remember this film,it was the first film i had watched at the cinema the picture was dark in places i was very nervous it was back in 74/75 my Dad took me my brother & sister to Newbury cinema in Newbury Berkshire England. I recall the tigers and the lots of snow in the film also the appearance of Grizzly Adams actor Dan Haggery i think one of the tigers gets shot and dies. If anyone knows where to find this on DVD etc please let me know.The cinema now has been turned in a fitness club which is a very big shame as the nearest cinema now is 20 miles away, would love to hear from others who have seen this film or any other like it.
Anonymized Review: I remember this film,it was the first film i had watched at the cinema the picture was dark in places i was very nervous it was back in 74/75 my Dad took me my brother & sister to Newbury cinema in Newbury Berkshire England. I recall the tigers and the lots of snow in the film also the appearance of Grizzly Adams actor Bla

Original Review: "Ardh Satya" is one of the finest film ever made in Indian Cinema. Directed by the great director Govind Nihalani, this one is the most successful Hard Hitting Parallel Cinema which also turned out to be a Commercial Success. Even today, Ardh Satya is an inspiration for all leading directors of India.<br /><br />The film tells the Real-life Scenario of Mumbai Police of the 70s. Unlike any Police of other cities in India, Mumbai Police encompasses a Different system altogether. Govind Nihalani creates a very practical Outlay with real life approach of Mumbai Police Environment.<br /><br />Amongst various Police officers & colleagues, the film describes the story of Anand Velankar, a young hot-blooded Cop coming from a poor family. His father is a harsh Police Constable. Anand himself suffers from his father's ideologies & incidences of his father's Atrocities on his mother. Anand's approach towards immediate action against crime, is an inert craving for his own Job sati

Original Review: One of the most significant quotes from the entire film is pronounced halfway through by the protagonist, the mafia middle-man Titta Di Girolamo, a physically non-descript, middle-aged man originally from Salerno in Southern Italy. When we're introduced to him at the start of the film, he's been living a non-life in an elegant but sterile hotel in the Italian-speaking Canton of Switzerland for the last ten years, conducting a business we are only gradually introduced to. While this pivotal yet apparently unremarkable scene takes place employees of the the Swiss bank who normally count Di Girolamo's cash tell him that 10,000 dollars are missing from his usual suitcase full of tightly stacked banknotes. At the news, he quietly but icily threatens his coaxing bank manager of wanting to close down his account. Meanwhile he tells us, the spectators, that when you bluff, you have to bluff right through to the end without fear of being caught out or appearing ridiculous. He s

Original Review: ***SPOILERS*** All too, in real life as well as in the movies, familiar story that happens to many young men who are put in a war zone with a gun, or rifle, in their hands. The case of young and innocent, in never handling or firing a gun, Jimmy Davis, Franchot Tone, has been repeated thousands of times over the centuries when men, like Jimmy Davis, are forced to take up arms for their country.<br /><br />Jimmy who at first wanted to be kicked out of the US Army but was encouraged to stay, by being belted in the mouth, by his good friend Fred P. Willis, Spencer Tracy, ended up on the front lines in France. With Jimmy's unit pinned down by a German machine gun nest he single handedly put it out of commission picking off some half dozen German soldiers from the safety of a nearby church steeple. It was when Jimmy gunned down the last surviving German, who raised his arms in surrender, that an artillery shell hit the steeple seriously wounding him.<br /><br />Recovering f

...

Original Review: i think the team behind this film did a very good job with the limitations they had. only £300,000 and 7 weeks to write, film and edit the whole thing which i think is an achievement in itself. although this film is not for the masses (as a young innocent teenage girl is killed and there is homo-eroticism involved in the story) i think that this film is a heart wrenching tragedy and the more deeply involved you get in the story, the more sadness you feel. more so towards Heaton because of the love he feels but is not returned.<br /><br />this is one of my favourite British films that i enjoyed very much and would watch again. i think that it's a shame that is film is not very well heard of at all.
Anonymized Review: i think the team behind this film did a very good job with the limitations they had. only £300,000 and 7 weeks to write, film and edit the whole thing which i think is an achievement in itself. although this film is not for the masses (as a young innocent t

Original Review: 'Presque Rien' ('Come Undone') is an earlier work by the inordinately gifted writer/ director Sébastien Lifshitz (with the collaboration of writer Stéphane Bouquet - the team that gave us the later 'Wild Side'). As we come to understand Lifshitz's manner of storytelling each of his works becomes more treasureable. By allowing his tender and sensitive love stories to unfold in the same random fashion found in the minds of confused and insecure youths - time now, time passed, time reflective, time imagined, time alone - Lifshitz makes his tales more personal, involving the viewer with every aspect of the characters' responses. It takes a bit of work to key into his method, but going with his technique draws us deeply into the film.<br /><br />Mathieu (handsome and gifted Jérémie Elkaïm) is visiting the seaside for a holiday, a time to allow his mother (Dominique Reymond) to struggle with her undefined illness, cared for by the worldly and wise Annick (Marie Matheron) and

Original Review: When a rich tycoon is killed in a plane crash, his spinster twin sister, Martha Craig (Madge Kennedy), doesn't believe he grabbed the controls in a suicide dive (even though self-snuff runs in the family) but his three beautiful daughters couldn't care less. The pilot, Jim Norton (John Bromfield), goes to work for Valerie Craig (Kathleen Hughes) who soon coerces him into helping her wrest control of the estate from her troubled sister, Lorna (Sara Shane) and the family lawyer (Jess Barker). Valerie wants Norton to seduce Lorna when he's not fending off the advances of another sister, the nymphet Vicki (Marla English), but her plans are thrown into a tailspin when Norton falls for his prey. All bets are off as a world of woe -including corporate chicanery, seductions, suicides, blackmail, a murder plot, the Mann Act, double-crosses, disfigurement, and poetic justice- befall "Craig Manor", an imposing mansion on a bluff overlooking the sea...<br /><br />This preposterous

Original Review: What more can be said? I have not been this fascinated with a young actress since Cate Blanchett burst upon the scene over ten years ago. And although both Blanchett and Blunt have played Queens now( seems to be the benchmark for up and coming actresses), the roles are complete polar opposites.<br /><br />Simply put if you are looking for high passion, compelling drama, and Machiavellian intrigue, this is not the movie for you. This isn't to say that the script or direction was bad, its just that the subject of the film did not lead too dramatic a life when compared to other notable royals like Elizabeth I, Anne Boylen, Henry VIII, Henry V, Henry II and Elainor of Acquitane. These are people whose lives were the stuff such as good soap operas are made of and whose policies and decisions altered the course of British ,and in most cases, world history. Victoria, in contrast, ascended the throne without incident, she quasi-governed a nation that was fast becoming a global

Original Review: I'm a fan of Judy Garland, Vincente Minnelli, and Gene Kelly, but this movie just left me cold. I was expecting another American In Paris from Minnelli, so perhaps I was expecting too much.<br /><br />The movie was short on songs and short of impressive dance numbers. I was impressed by the very expressionistic Kelly dance as Mococo on the ship. I was also impressed by the Nicholas Brothers in Be a Clown, too bad the song was so annoying. I also enjoyed Judy attacking Kelly with bric-a-brac. Check Lorna Luft's autobiography for some interesting information on that scene.<br /><br />Actually, the movie has what must be some of Cole Porter's most annoying songs, especially "Nina". Also, Judy and Gene yell constantly like screechy children.<br /><br />The plot is thin--which is par for the course for musicals--but it is not saved by impressive dance numbers or by memorable songs. I suspect the best parts of this movie were left on the cutting room floor. Please, some movi

In [5]:
fieldnames = ['Review', 'Sentiment']

# Combine data into a list of dictionaries
rows = [{'Review': review, 'Sentiment': sentiment} for review, sentiment in zip(processed_rows, processed_rows_sent)]

# Writing data to the CSV file
with open('IMDB_anonymized_data.csv', 'w', newline='') as csvfile:
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
    writer.writeheader()  # Write header
    for row in rows:
        writer.writerow(row)

print("CSV file created successfully.")

CSV file created successfully.


In [6]:
print("Entity Type Counts:")
for entity_type, count in entity_type_counts.items():
    print(f"{entity_type}: {count}")

Entity Type Counts:
PERSON: 16023
LOCATION: 2519
NRP: 1819
URL: 562
DATE_TIME: 3901
IN_PAN: 1610
US_DRIVER_LICENSE: 7
US_BANK_NUMBER: 1
EMAIL_ADDRESS: 2
IP_ADDRESS: 2


In [1]:
import nltk
import pandas as pd
import numpy as np
from collections import Counter
from sklearn.metrics.pairwise import cosine_similarity
import gensim.downloader as api

# Download necessary resources from NLTK
nltk.download('punkt')

# Load Word2Vec model
model = api.load("word2vec-google-news-300")

# Function to calculate word similarity
def word_similarity(word, word_list, model):
    try:
        # Get word embedding for the word
        word_embedding = model[word]

        # Get word embeddings for the word list
        word_list_embeddings = [model[w] for w in word_list]

        # Calculate cosine similarity between the word and word list
        similarities = cosine_similarity([word_embedding], word_list_embeddings)

        # Return the average similarity score
        return np.mean(similarities)

    except KeyError:
        # Return 0 if word is not present in the vocabulary
        return 0

# load dataset
df = pd.read_csv("anonmyised_tweet_emotions.csv")

data = df['content'][:3000]

# Tokenize words in the dataset
tokenized_data = [nltk.word_tokenize(sentence.lower()) for sentence in data]

# Flatten the list of tokenized words
all_words = [word for sentence in tokenized_data for word in sentence]

# Calculate word frequency
word_counts = Counter(all_words)

# Calculate the 1st percentile of word frequencies
percentile_1 = np.percentile(list(word_counts.values()), 1)

# Calculate similarity scores and store in a dictionary
similarity_dict = {}
for word in all_words:
    if word not in similarity_dict:
        similarity_dict[word] = word_similarity(word, all_words, model)

# Calculate the 1st percentile threshold for similarity scores
percentile_similarity_threshold = np.percentile(list(similarity_dict.values()), 1)

# Identify outlier words based on the 1st percentile threshold
outlier_words = [word for word, count in word_counts.items() if count <= percentile_1 and similarity_dict[word] <= percentile_similarity_threshold]

print("Outlier words (occurring less frequently than 1% of words and less similar):", outlier_words)

# Write the original sentences containing the words detected as outliers
for sentence in data:
    for word in nltk.word_tokenize(sentence.lower()):
        if word in outlier_words:
            print("Outlier word:", word)
            print("Outlier sentence:", sentence)
            break  # Break out of inner loop once an outlier word is found in the sentence


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


Outlier words (occurring less frequently than 1% of words and less similar): ['tiffanylue', 'listenin', 'habit', 'layin', 'ughhhh', 'waitin', 'ceremony', 'gloomy', 'dannycastillo', 'houston', 're-pinging', 'ghostridah14', 'scandalous', '//www.djhero.com/', 'charviray', 'moorerlene', 'kelcouch', 'choked', 'retainers', 'brodyjenner', 'realise', 'tourture', 'itonlinelol', 'annarosekerr', 'perezhilton', 'leaking', 'signals', 'raaaaaaek', '7am', 'plotting', 'plots', 'muahahaha', 'talks', 'balisage', 'markup', 'conference', 'program', '//tr.im/ml6z', 'bobdc', 'topicmaps', 'infection', 'underage', 'keggers', 'isaacmascote', 'isaac', 'manners', 'lewd', 'damm', 'koxpers', 'fudge', 'cynthia_123', 'bl', 'contractions', '//plurk.com/p/wxidk', 'stoked', 'davidbrussee', 'skott', 'gabbyisactive', 'unfollow', 'uds', 'fred', 'owensarchie', 'perform', 'sfo', 'creyes', 'elem', 'remain', 'credits', 'onscrn', 'separate', 'amf', 'jakeboyd', 'reaaaally', 'batman', 'wnna', 'djmicdamn', 'fucker', 'textd', 'men

In [2]:
import pandas as pd
from sklearn.impute import SimpleImputer
from sklearn.neighbors import LocalOutlierFactor
from sklearn.preprocessing import LabelEncoder, StandardScaler

def detectOutliers(df):
      # Handle missing values
      imputer = SimpleImputer(strategy='mean')
      numeric_columns = df.select_dtypes(include=['int', 'float']).columns
      df[numeric_columns] = imputer.fit_transform(df[numeric_columns])

      # Separate numeric and non-numeric columns
      numeric_columns = df.select_dtypes(include=['int', 'float']).columns
      non_numeric_columns = df.select_dtypes(exclude=['int', 'float']).columns

      # Encode non-numeric columns
      label_encoder = LabelEncoder()
      for col in non_numeric_columns:
          df[col] = label_encoder.fit_transform(df[col])

      kmeans = KMeans(n_clusters=4)  # Adjust the number of clusters as needed
      df['NumericCluster'] = kmeans.fit_predict(df)
      print(df)
      # Standardize numeric columns
      scaler = StandardScaler()
      df[numeric_columns] = scaler.fit_transform(df[numeric_columns])

      # Concatenate encoded non-numeric column with standardized numeric columns
      X = df.values

      # Apply Local Outlier Factor
      lof = LocalOutlierFactor(n_neighbors=5, contamination=0.1) # Adjust parameters as needed
      outlier_scores = lof.fit_predict(X)

      # Identify outliers
      outliers = df[outlier_scores == -1]
      print("Outliers:")
      print(outliers)
      return outliers


In [3]:
import numpy as np

def find_nearest_record(record, cluster_data):
    min_distance = np.inf
    nearest_record = None
    nearest_index = None

    for index, row in cluster_data.iterrows():
        if not np.array_equal(row.values, record.values):
            distance = np.linalg.norm(record - row)
            if distance < min_distance:
                min_distance = distance
                nearest_record = row
                nearest_index = index

    return nearest_record, nearest_index



In [7]:
from sklearn.cluster import KMeans

df = pd.read_csv("assignment_data.csv")
outliers=detectOutliers(df)
record,index=find_nearest_record(outliers.iloc[0],df)

print(index)


row_index = df.index[(df == (outliers.iloc[0])).all(axis=1)]

if not row_index.empty:
    print("Index of the row with target values:", row_index[0])
else:
    print("No row found with the target values.")

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(


      athlete_id  name  region  affiliate  gender  age  height  candj  \
0           1883   135      13       1607       1    0       1      4   
1            901  1651      15       1112       1    1       1      2   
2           1279  2318       8        662       1    3       3      4   
3           1261   628       8        509       1    4       4      1   
4            297  1749       9        610       1    1       3      4   
...          ...   ...     ...        ...     ...  ...     ...    ...   
2457         111   363      14        221       1    4       0      1   
2458         663   254       4        252       1    4       4      2   
2459         499    18      15        386       1    3       3      3   
2460         599  1572       9       1176       0    0       1      0   
2461        2324   863       9        332       0    3       0      0   

          snatch  deadlift  backsq  train  experience  howlong  NumericCluster  
0     239.842172         4       4     17 

In [3]:
import re
import pandas as pd
from presidio_analyzer import AnalyzerEngine
from faker import Faker

fake = Faker()
analyzer = AnalyzerEngine()

def anonymize_text(text):

    results = analyzer.analyze(text, language='en', entities=["PERSON", "EMAIL_ADDRESS"])


    for result in results:
        if result.entity_type == "PERSON":
            print(result)
            fake_name = fake.name()
            text = text[:result.start] + fake_name + text[result.end:]


    text = re.sub(r'\b[A-Za-z0-9._%+-]+@[A-Za-z0-9.-]+\.[A-Z|a-z]{2,}\b', '[EMAIL]', text)
    print(text)

    return text


df = pd.read_csv("tweet_emotions.csv")[:3000]


df['content'] = df['content'].apply(anonymize_text)


print(df[['content']])


type: PERSON, start: 0, end: 11, score: 0.85
Scott Mann i know  i was listenin to bad habit earlier and i started freakin at his part =[
Layin n bed with a headache  ughhhh...waitin on your call...
Funeral ceremony...gloomy friday...
wants to hang out with friends SOON!
@dannycastillo We want to trade with someone who has Houston tickets, but no one will.
type: PERSON, start: 53, end: 55, score: 0.85
Re-pinging @ghostridah14: why didn't you go to prom? William Grant my bf didn't like my friends
I should be sleep, but im not! thinking about an old friend who I want. but he's married now. damn, &amp; he wants me 2! scandalous!
Hmmm. http://www.djhero.com/ is down
type: PERSON, start: 0, end: 19, score: 0.85
Mary Nelson my love. I miss you
@kelcouch I'm sorry  at least it's Friday?
cant fall asleep
Choked on her retainers
Ugh! I have to beat this stupid song to get to the next  rude!
@BrodyJenner if u watch the hills in london u will realise what tourture it is because were weeks and week

Got the news
The storm is here and the electricity is gone
@annarosekerr agreed
So sleepy again and it's not even that late. I fail once again.
@PerezHilton lady gaga tweeted about not being impressed by her video leaking just so you know
How are YOU convinced that I have always wanted you? What signals did I give off...damn I think I just lost another friend
@raaaaaaek oh too bad! I hope it gets better. I've been having sleep issues lately too
Wondering why I'm awake at 7am,writing a new song,plotting my evil secret plots muahahaha...oh damn it,not secret anymore
No Topic Maps talks at the Balisage Markup Conference 2009   Program online at http://tr.im/mL6Z (via @bobdc) #topicmaps
I ate Something I don't know what it is... Why do I keep Telling things about food
so tired and i think i'm definitely going to get an ear infection.  going to bed &quot;early&quot; for once.
On my way home n having 2 deal w underage girls drinking gin on da bus while talking bout keggers......damn i feel o

type: PERSON, start: 80, end: 87, score: 0.85
Looks like another sleepless night dedicated to homework. Sorry in advance, Ms. Kristine Reynolds.
@jessicaduncan http://twitpic.com/662vk -  WHY DO U LOT MOCK ME!!!
didnt say goodnight to you
@abguerraartist  I am not a pussy! damnit!  [sending you an e-mail right now btw]
type: PERSON, start: 9, end: 12, score: 0.85
has work Victor Meyer.
In the Hongkong International Airport. Has to wait for 3-4 hours for our next flight to Cebu.
Can't sleep and nothings on tv!!
type: PERSON, start: 55, end: 60, score: 0.85
type: PERSON, start: 108, end: 113, score: 0.85
The pics I just uploaded are the baby pics of my cats. Lisa Reynolds is now an adult and a pretty little kitJames Moralesut Batty is in kitten heaven now
@KallieT oh ... you've been superseeded?  not good enough
today we say goodbye to the second good friend in a week from dmp  but at least the sun is shinning and I'm definately NOT working this pm
fuckin'm transtelecom
is really, really

Is ANYBODY up? .... I'm sooo bored!
@AmandaMallard i'm not at chaseton's either  please don't die, my heart will be really sad
that was an interesting show to say the least. recap tomorrow. first i must sleep. work in am.
@omgjoker o its feels like a hot box and no matter where i go in here it still feels like a hot box! ice cream isn't working n e more
type: PERSON, start: 31, end: 38, score: 0.85
Very Sad.... please get better James Duncan
type: PERSON, start: 0, end: 20, score: 0.85
Travis Perezi hate everything
Gosh. Today's weather is HOrriTerrible! Extreme hotness. I'm losing a lot of water weight by doing nothing.  - http://tweet.sg
Is taking a moment to reflect...I want my annonymity back,FB!!!!  Is it safe to say anything about someone else to another friend again?
type: PERSON, start: 19, end: 24, score: 0.85
@pastorpeterko Hey Jeremy Ray, thanks for the follow. So many Sydney pastors tweet!!! Shame no Bris pastors are on Twitter; we're behind.
@sha_da_asshole ï¿½ cant im not

@narain Dun wanna travel all the way there for lunch now. But yeah i have been there. Nice place. Missing Shan-e-Punjab though...
Doing a mass cleanout of my room before rearranging it. Just sent mother out to buy me a bin and a bookshelf since mine sucks. Bad mood
@xMyLifesAStoryx rob got lucky that game he beat me 209-205
feeling really sick  watching the fifth element, and about to smoke a cigg. ugh i hate colds!
Bah I don't think @bing's FB fan page will get to 7500
someone save me!! i dont want to pack anymore
home from school had the shitest day today
@markiti The sweety sat on the table this morning...Just woke up! Very sweet! Oh...btw...I think i'll be home around 7 pm!!!  Xxx
bruise on knee will make it hard to skate tomorrow.
@hobosexual lol.  When I went to buy my new laptop in Feb., I already knew, lol, but I looked anyway and walked away sadfaced. :/
FYI no internets until THURSTAG!!!! after saturday  i have a feeling i will become 800x more productive during those days.
S

...

@bbyowls i cant afford it  go to school here ? !!
Too broke for cigarettes.
@kimberly__joy i feel like red lea now
squirrel! where? i hate squirrels
@grantarnow WHY DIDNT I SEE YOU?
Just watched Mall Cop. Wasn't that funny, but wasn't too bad. I guess. I kinda wish I still worked at a movie theater....
type: PERSON, start: 59, end: 63, score: 0.85
Can't sleep....  &amp; why isn't my $ in my damn account!? Kimberly Cruz is trippin
@tissuerose i'm with you in this.  i've always have prob prioritizing myself ahead of him.
Morning twitties! Heading to college, just back from the docs, god I'm hungry  streching my ears again today! 10mm ;) payday I love you!
backache
Five o'clock can't come any faster
Finishing the video. Fuck me, it's so long
LAPPYTOP BATERRRY DYING,tryingtofind a movieto watch since im staying in.  and goingto my room.
type: PERSON, start: 0, end: 7, score: 0.85
Dr. Taylor Fletcher willie of fortune is just making me depressed  damn love.
type: PERSON, start: 0, end: 8, s

The sun is shining and I'm stuck in work
...I have to study ....
Just been bitten by SmoothStreaming, it doesn't seem to work for my client's linux users...fan-fricking-tastic
@pyroezra idk if i could.  it would cost me soo much there.
? MADAYA KA CHRISTIAN. BLEH!!! I HATE U  http://plurk.com/p/wy2yg
Squabbling with people over the internet is great for my Tumblarity, but bad for my ego when they have more internet friends than me
Wow, been away 4 a while...stupid lap top is in the shop...still    Hope everyone is well!
Type cold in my room
Desperately wishing I could sleep - But I am too frazzled about my Gma, and can't sleep.. :'( It's really bad tonight  xx
Planning a road trip down to San Diego- With a detour into Vegas to celebrate my birthday! Too bad it's 7 wks away  I want to go now!
is MySpace mobile free? or do u have 2 have credit... cause they are liers
@MaryKathrynK Yikes!  I hope she was okay.  I never her heard her say her tummy hurt.
@MAGUSWEAVER don't follow me. You wi

Weather is back to being great! Shame I have to wait in for my delivery
@Jonasbrothers movie out today but i cant go see it
In trouble - I haven't finished reading Crow Road  Book Club's off for me today I'm afraid. Lazy mare.
wishing my days off were the same days that people wanted to party.
@capricious_and IKR. I myself am headed out for a meeting.
@HoneyJune k... i guess i cant help it.... byeee 4eva....  (m really sad)
leave for calcutta-delhi-lucknow tomorrow...10 days of absence!!!
I hate the &quot;out-of-nowhere&quot; stuff...
Been rebuilding my Dev. machine after a disk crash last night
type: PERSON, start: 131, end: 138, score: 0.85
@haylescakes Sis...I dont think I will be up 4 2nite sadly  Im in alot of pain 2day &amp; had bad nite...can we go out anotha week Philip Duke
I can't believe it's 9am and i'm awake, and i have to start getting ready soon. I hate the doctor's
sick n tired of people who steal other people's work
type: PERSON, start: 60, end: 78, score: 0.85
@SeandB

type: PERSON, start: 110, end: 115, score: 0.85
@theJBs @wearecutaways  We were all set to get a room last Saturday! I can't apologise enough for missing out Toni Wells
@aravindkumar Whats up today..? missed the #coffeeclub that day
type: PERSON, start: 0, end: 10, score: 0.85
Dustin Anderson That was a horrible day.
I wanna see the Jonas Brothers in concert..
@zoecorkhill do you get headaches a lot? What painkillers do you take? Nothing works for mine
@iamdiddy I don't think they sale Ciroc where I stay..Damn..thats just my luck
Last day in Dijon
Back on track with the transcription process. Still can't stop my lappy overheating, though
feels very, very rough!
Tucking myself in tonight  Mogwai on repeat
type: PERSON, start: 0, end: 17, score: 0.85
Ashley Connerm pooped from moving 2day im just laying down relaxing  lol
@ferretwho Defeated by a Polo
fine, i give in, docs again today. not being able to breath this morning made me think i should. hate docs
Tuesday, Wednesday, Thursday an

cant take photos of Darling Harbour fireworks cause its raining  carried all my camera gear to work for nothing #fb
just woke up, and my tummy hurts  there's always something wrong with me :S
type: PERSON, start: 17, end: 23, score: 0.85
@MrsSOsbourne Hi Monique Krueger Missed you on our x factor last year!!  Come Back!! x
3-4 hours sleep last night  barely functioning
Seems like 60 min wait time  should I call the wife now
@tahninial just called me a cheeseburglar. He made me sad
Not happy got a big choice to make
Getting bored sitting at the hotel room the entire day
type: PERSON, start: 5, end: 15, score: 0.85
It's Robert Clark last Friday today
type: PERSON, start: 0, end: 3, score: 0.85
type: PERSON, start: 22, end: 26, score: 0.85
Alicia Sweeney, am dinThomas White PR 4. Yeey, my epenis is now bigger! ... ... ...
@Sarahies I will be ok when I have been to the drs again today and got my essay done  x howre you?? x
Hmm... I should go make a time machine to go forward to 12:00 God i

In [4]:
import re
import pandas as pd
import numpy as np
from datetime import datetime, timedelta
from dateutil.parser import parse

def anonymize_text(text):
    # Function to generalize ages
    def generalize_ages(ages):
        age_groups = []
        for age in ages:
            if age < 20:
                age_groups.append("Teenager")
            elif 20 <= age < 30:
                age_groups.append("20s")
            elif 30 <= age < 40:
                age_groups.append("30s")
            elif 40 <= age < 50:
                age_groups.append("40s")
            elif 50 <= age < 60:
                age_groups.append("50s")
            elif 60 <= age < 70:
                age_groups.append("60s")
            else:
                age_groups.append("Senior")
        return age_groups


    def perturb_dates(dates):
        perturbed_dates = []
        for date in dates:
            random_shift = timedelta(days=np.random.randint(-7, 8))  # Random shift up to 7 days
            perturbed_date = date + random_shift
            perturbed_dates.append(perturbed_date)
        return perturbed_dates

    def anonymize_elements(text):
        text = re.sub(r'@\w+', '[USERNAME]', text)
        return text

    def apply_anonymization(text):
        anonymized_text = anonymize_elements(text)

        age_pattern = r'\b(\d{1,2})\s*(?:years?|yrs?)\b'  # Regular expression to find ages
        ages = re.findall(age_pattern, anonymized_text)  # Find all occurrences of ages
        ages = [int(age) for age in ages]  # Convert ages to integers
        generalized_ages = generalize_ages(ages)  # Generalize ages


        # Replace ages with generalized ranges
        for age, generalized_age in zip(ages, generalized_ages):
            print(age)
            print(anonymized_text)
            print(generalized_age)
            anonymized_text = anonymized_text.replace(str(age), generalized_age)
            print(anonymized_text)

        return anonymized_text
    anonymized_text = apply_anonymization(text)

    return anonymized_text


df['content'] = df['content'].apply(anonymize_text)
print(df[['content']])


4
[USERNAME] PGPM student from where? I myself was a PGPM student about 4 years back. I wish I could stay one
Teenager
[USERNAME] PGPM student from where? I myself was a PGPM student about Teenager years back. I wish I could stay one
2
i no i no bt i had only been a gamer for like 2 years when i made that attempt  lol yea i luvd F1 to an extent [USERNAME]
Teenager
i no i no bt i had only been a gamer for like Teenager years when i made that attempt  lol yea i luvd F1 to an extent [USERNAME]
30
is tryna find her a 30 yr old junt with a 401 k, stable job, good home with an extra room 4 me and my baggage..so tired of u young dudes
30s
is tryna find her a 30s yr old junt with a 401 k, stable job, good home with an extra room 4 me and my baggage..so tired of u young dudes
3
[USERNAME] still on track to move back, albeit in 2-3 years.  However, my buddy Kimberly Long is now moving with me, so we're on a FAST track!
Teenager
[USERNAME] still on track to move back, albeit in 2-Teenager years. 

In [5]:
original_dataframe=pd.read_csv("tweet_emotions.csv")
anonymized_dataframe=df

def jaccard_similarity(set1, set2):
    intersection = len(set1.intersection(set2))
    union = len(set1.union(set2))
    return intersection / union if union != 0 else 0

# Example function to tokenize text into sets of words
def tokenize(text):
    return set(text.split())

# Calculate Jaccard similarity for each pair of original and anonymized text
similarities = []
for original_text, anonymized_text in zip(original_dataframe['content'], anonymized_dataframe['content']):
    original_tokens = tokenize(original_text)
    anonymized_tokens = tokenize(anonymized_text)
    similarity = jaccard_similarity(original_tokens, anonymized_tokens)
    similarities.append(similarity)

# Calculate average similarity
average_similarity = sum(similarities) / len(similarities)
print("Average Jaccard Similarity:", average_similarity)


Average Jaccard Similarity: 0.8912420992511267


In [6]:
import pandas as pd


anonymized_data = df

unique_records = anonymized_data.nunique()
print(unique_records)

proportion_unique = unique_records / len(anonymized_data)

risk_of_deanonymization = 1 - proportion_unique.mean()

print(risk_of_deanonymization)

tweet_id     3000
sentiment      13
content      2995
dtype: int64
0.33244444444444454


In [7]:
import pandas as pd

# Load the original and anonymized datasets
original_data = pd.read_csv("tweet_emotions.csv")[:3000]

# Calculate the information loss
total_unique_records_original = len(original_data.drop_duplicates())
total_unique_records_anonymized = len(anonymized_data.drop_duplicates())
print(total_unique_records_original)

information_loss = (total_unique_records_original - total_unique_records_anonymized) / total_unique_records_original

# Analyze the information loss
print("Information Loss:", information_loss)


3000
Information Loss: 0.0


In [8]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.cluster import KMeans

def analyze_anonymized_text(anonymized_df):
    # Step 1: Load anonymized dataset

    # Step 2: Calculate TF-IDF vectors for anonymized text
    tfidf_vectorizer = TfidfVectorizer()
    tfidf_matrix = tfidf_vectorizer.fit_transform(anonymized_df['content'])

    # Step 3: Calculate cosine similarity between records
    similarity_matrix = cosine_similarity(tfidf_matrix, tfidf_matrix)

    # Step 4: Assess uniqueness of anonymized records
    threshold = 0.8  # Define similarity threshold
    unique_records = sum(similarity_matrix.diagonal() > threshold)  # Count records with high self-similarity
    total_records = len(anonymized_df)
    uniqueness_ratio = unique_records / total_records

    # Step 5: Analyze statistical properties
    word_counts = anonymized_df['content'].str.split().apply(len)
    average_word_count = word_counts.mean()

    # Step 6: Perform clustering analysis
    kmeans = KMeans(n_clusters=3, random_state=42)
    clusters = kmeans.fit_predict(tfidf_matrix)
    cluster_distribution = pd.Series(clusters).value_counts()

    return uniqueness_ratio, average_word_count, cluster_distribution




In [9]:

uniqueness_ratio, average_word_count, cluster_distribution = analyze_anonymized_text(df)
print("Uniqueness Ratio:", uniqueness_ratio)
print("Average Number of Words per Record:", average_word_count)
print("Cluster Distribution:", cluster_distribution)

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(


Uniqueness Ratio: 0.9996666666666667
Average Number of Words per Record: 13.725333333333333
Cluster Distribution: 2    1599
0     792
1     609
dtype: int64


In [10]:
uniqueness_ratio, average_word_count, cluster_distribution = analyze_anonymized_text(pd.read_csv("anonmyised_tweet_emotions.csv")[:3000])
print("Uniqueness Ratio:", uniqueness_ratio)
print("Average Number of Words per Record:", average_word_count)
print("Cluster Distribution:", cluster_distribution)

Uniqueness Ratio: 0.9996666666666667
Average Number of Words per Record: 13.794
Cluster Distribution: 0    1719
2     664
1     617
dtype: int64


/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(


In [12]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler

def analyze_anonymized_data(anonymized_df):
    # Step 1: Separate numeric and string fields
    numeric_columns = anonymized_df.select_dtypes(include=['number']).columns
    string_columns = anonymized_df.select_dtypes(include=['object']).columns

    # Step 2: Analyze numeric fields
    numeric_statistics = anonymized_df[numeric_columns].describe()

    # Step 3: Analyze string fields
    string_statistics = {}
    for column in string_columns:
        # Calculate TF-IDF vectors for string fields
        tfidf_vectorizer = TfidfVectorizer()
        tfidf_matrix = tfidf_vectorizer.fit_transform(anonymized_df[column].astype(str))

        # Calculate cosine similarity between records
        similarity_matrix = cosine_similarity(tfidf_matrix, tfidf_matrix)

        # Assess uniqueness of anonymized records
        threshold = 0.8  # Define similarity threshold
        unique_records = sum(similarity_matrix.diagonal() > threshold)  # Count records with high self-similarity
        total_records = len(anonymized_df)
        uniqueness_ratio = unique_records / total_records

        # Analyze statistical properties
        word_counts = anonymized_df[column].str.split().apply(len)
        average_word_count = word_counts.mean()

        string_statistics[column] = {'uniqueness_ratio': uniqueness_ratio, 'average_word_count': average_word_count}

    # Step 4: Perform clustering analysis on numeric fields
    numeric_clusters = None
    if not numeric_columns.empty:
        scaler = StandardScaler()
        scaled_numeric_data = scaler.fit_transform(anonymized_df[numeric_columns])
        kmeans = KMeans(n_clusters=3, random_state=42)
        numeric_clusters = kmeans.fit_predict(scaled_numeric_data)
        numeric_cluster_distribution = pd.Series(numeric_clusters).value_counts()
    else:
        numeric_cluster_distribution = None

    return numeric_statistics, string_statistics, numeric_clusters, numeric_cluster_distribution

# Example usage:
# Assuming 'df' contains the anonymized dataframe
numeric_statistics, string_statistics, numeric_clusters, numeric_cluster_distribution = analyze_anonymized_data(pd.read_csv("assignment_data.csv"))
print("Numeric Statistics:\n", numeric_statistics)
print("String Statistics:\n", string_statistics)
print("Numeric Clusters:\n", numeric_clusters)
print("Numeric Cluster Distribution:\n", numeric_cluster_distribution)


TypeError: object of type 'float' has no len()

In [14]:
import pandas as pd
from sklearn.impute import SimpleImputer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler

def analyze_anonymized_data(anonymized_df):
    # Step 1: Separate numeric and string fields
    numeric_columns = anonymized_df.select_dtypes(include=['number']).columns
    string_columns = anonymized_df.select_dtypes(include=['object']).columns

    # Step 2: Impute missing values in numeric data
    imputer = SimpleImputer(strategy='mean')
    anonymized_df[numeric_columns] = imputer.fit_transform(anonymized_df[numeric_columns])

    # Step 3: Analyze numeric fields
    numeric_statistics = anonymized_df[numeric_columns].describe()

    # Step 4: Analyze string fields
    string_statistics = {}
    for column in string_columns:
        # Calculate TF-IDF vectors for string fields
        tfidf_vectorizer = TfidfVectorizer()
        tfidf_matrix = tfidf_vectorizer.fit_transform(anonymized_df[column].astype(str))

        # Calculate cosine similarity between records
        similarity_matrix = cosine_similarity(tfidf_matrix, tfidf_matrix)

        # Assess uniqueness of anonymized records
        threshold = 0.8  # Define similarity threshold
        unique_records = sum(similarity_matrix.diagonal() > threshold)  # Count records with high self-similarity
        total_records = len(anonymized_df)
        uniqueness_ratio = unique_records / total_records

        # Analyze statistical properties
        word_counts = anonymized_df[column].astype(str).str.split().apply(len)
        average_word_count = word_counts.mean()

        string_statistics[column] = {'uniqueness_ratio': uniqueness_ratio, 'average_word_count': average_word_count}

    # Step 5: Perform clustering analysis on numeric fields
    numeric_clusters = None
    numeric_cluster_distribution = None
    if not numeric_columns.empty:
        scaler = StandardScaler()
        scaled_numeric_data = scaler.fit_transform(anonymized_df[numeric_columns])
        kmeans = KMeans(n_clusters=3, random_state=42)
        numeric_clusters = kmeans.fit_predict(scaled_numeric_data)
        numeric_cluster_distribution = pd.Series(numeric_clusters).value_counts()

    return numeric_statistics, string_statistics, numeric_clusters, numeric_cluster_distribution

# Example usage:
# Assuming 'df' contains the anonymized dataframe
numeric_statistics, string_statistics, numeric_clusters, numeric_cluster_distribution = analyze_anonymized_data(pd.read_csv("assignment_data.csv"))
print("Numeric Statistics:\n", numeric_statistics)
print("String Statistics:\n", string_statistics)
print("Numeric Clusters:\n", numeric_clusters)
print("Numeric Cluster Distribution:\n", numeric_cluster_distribution)


/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(


Numeric Statistics:
             snatch
count  2462.000000
mean    172.083679
std      64.092262
min      -0.008612
25%     136.415809
50%     165.209070
75%     204.984164
max    1936.028477
String Statistics:
 {'athlete_id': {'uniqueness_ratio': 1.0, 'average_word_count': 1.0}, 'name': {'uniqueness_ratio': 1.0, 'average_word_count': 2.291632818846466}, 'region': {'uniqueness_ratio': 1.0, 'average_word_count': 1.8899268887083671}, 'affiliate': {'uniqueness_ratio': 1.0, 'average_word_count': 2.376523151909017}, 'gender': {'uniqueness_ratio': 1.0, 'average_word_count': 1.0}, 'age': {'uniqueness_ratio': 1.0, 'average_word_count': 1.0}, 'height': {'uniqueness_ratio': 1.0, 'average_word_count': 1.0}, 'candj': {'uniqueness_ratio': 1.0, 'average_word_count': 1.0}, 'deadlift': {'uniqueness_ratio': 1.0, 'average_word_count': 1.0}, 'backsq': {'uniqueness_ratio': 1.0, 'average_word_count': 1.0}, 'train': {'uniqueness_ratio': 1.0, 'average_word_count': 13.172623883021933}, 'experience': {'uniquen